# Surface Wave Velocity (Single Station Approach)

In [ ]:
# Preparation: load packages, set some basic options  
%matplotlib inline
from obspy import UTCDateTime
from obspy.clients.fdsn import Client
from obspy.clients.fdsn import URL_MAPPINGS
import numpy as np
import matplotlib.pylab as plt
from movingWindow import movingWindowAnalysis, hann                      # import the moving window analysis routines
from multipleFilter import multipleFilterAnalysis, normalizeMFT                     # import the multiple filter analysis routines
plt.style.use('ggplot')
plt.rcParams['figure.figsize'] = 15, 4
plt.rcParams['lines.linewidth'] = 0.5

## Data from data archive using obspy webfdsn client
FDSN stands for the International Federal of Digital Seismic Networks (www.fdsn.org). Citation from their web site: "The International Federation of Digital Seismograph Networks (FDSN) is a global organization. Its membership is comprised of groups responsible for the installation and maintenance of seismographs either within their geographic borders or globally. Membership in the FDSN is open to all organizations that operate more than one broadband station. Members agree to coordinate station siting and provide free and open access to their data. This cooperation helps scientists all over the world to further the advancement of earth science and particularly the study of global seismic activity."
BGR (Bundesanstalt für Geowissenschaften und Rohstoffe) operates broadband stations in Germany and operates a data archive. It is member of the FDSN. That is why we can freely download data from them.
There are other data archives around the world which are also member of the FDSN and allow opn access to their data (see OBSPY documentation 

In [ ]:
for key in sorted(URL_MAPPINGS.keys()):                       # eine Liste der Archive
    print("{0:<7} {1}".format(key,  URL_MAPPINGS[key]))

Get waveforms for the Tohoku earthquake for station TNS of the German Regional Seismic Network.

In [ ]:
client = Client("BGR")                                          # data archive from which data are fetched
t1 = UTCDateTime("2018-01-14T09:19:00.000")                     # desired start time of data
stc = client.get_waveforms("GR", "TNS", "", "LHZ", t1,          # use fdsn web client to download data
                           t1 + 7200., attach_response=True)

In [ ]:
stc.detrend('linear')                       # take out linear trend
stc.plot()
print(stc)

In [ ]:
st = stc.copy()                                     # proceed with copy to avoid repeated downloading
ta = UTCDateTime("2018-01-14T10:05:00.000000Z")     # cut to surface wave train
te = UTCDateTime("2018-01-14T10:22:00.000000Z")
st.trim(ta,te)
st.taper(0.05,"hann")                               # apply a taper to bring signal to zero at ends
st.plot()                                           # dispersion is now well visible
print(st)
tr = st[0]

## Moving window approach

In [ ]:
wlen = 256.0                                                  # window length in sec
npts = tr.stats.npts                                          # number of samples in the trace
dt = tr.stats.delta                                           # sample interval
nwin = int(wlen/dt)                                           # nuber of samples in window
nwin = int(pow(2, np.ceil(np.log(nwin)/np.log(2))))           # find next higher power of 2 of nwin
shift = nwin//8
tshift = shift*dt
nseg,mwa = movingWindowAnalysis(tr.data,hann,nwin,shift,2.0)  # compute spectrogram, exponent=2.0
freq = np.fft.rfftfreq(nwin,dt)                               # Fourier frequencies
print("Frequency range [Hz]: ",freq[0],freq[-1])
print("Number of frequency samples: ",len(freq))
print("Window length in samples: ",nwin)
print("Window shift in samples: ",shift)
print("Number of segments: ",nseg)

In [ ]:
# plot the result
st.plot()                                                    # plot seismogram again
fmax = 0.08                                                  # maximum frequency to be plotted
fmin = 0.02
nf = len(freq)-1                                             # number of frequencies
jfmax = int(fmax/freq[-1]*nf)                                # max index for plotting 
jfmin = int(fmin/freq[-1]*nf)                                # min index for plotting 
extent = (0.5*wlen,0.5*wlen+nseg*tshift,fmin,fmax)           # extent of matrix in true time and frequency
asp = 0.5*nseg*tshift/(fmax-fmin)
fg = plt.figure(figsize = [12.5,12])
plt.imshow(mwa[jfmin:jfmax,:],extent = extent, aspect = asp, 
           origin = "lower", interpolation = "bicubic")      # plotting with interpolation
plt.xlabel('Window center time [s]')
plt.ylabel('Frequency [Hz]')
plt.show()

Observe the change of frequency content with time from 0.03 Hz initially to 0.06 Hz towards the end of the record. Given a epicentral distance $d$, we could transform the time axis into a group velocity axis via $U=d/t$.

## Multiple filtering approach

In [ ]:
alfa = 50.0                                             # filter width parameter
cfreq = np.linspace(fmin,fmax,100)                      # array of filter center frequencies
mfa = multipleFilterAnalysis(tr.data,alfa,cfreq,dt,1)
mfa = normalizeMFT(mfa,'freq',2.0)

In [ ]:
st.plot()
fg = plt.figure(figsize = [12.5,12])
extent = (0.,npts*dt,fmin,fmax)                         # extent of matrix in true time and frequency
asp = 0.5*npts*dt/(fmax-fmin)
plt.imshow(mfa,extent = extent, aspect = asp, 
           origin = "lower", interpolation = "bicubic")    # plotting
plt.xlabel('Time [s]')
plt.ylabel('Frequency [Hz]')
plt.show()